In [3]:
import pandas as pd
import numpy as np
import plotly.express as px
import requests
from urllib.parse import quote_plus
import requests_cache
from retrying import retry
import xml.etree.ElementTree as ET
from tqdm import tqdm

In [4]:
test_url = "https://eutils.ncbi.nlm.nih.gov/entrez/eutils/esearch.fcgi?db=pubmed&term=(%22VH%22%20)&retmax=0"

response = requests.get(test_url)


In [5]:
merged_alias_overlap_df_2 = pd.read_csv('merged_alias_overlap_df_2.csv')
merged_alias_overlap_df_2

Unnamed: 0 alias_symbol  \
0            3260           VH   
1            1284        H4-16   
2            1288        H4C13   
3            1285         H4C1   
4            1287        H4C12   
...           ...          ...   
10423        2234         OTF3   
10424        2233          OSX   
10425        2232        OSTCL   
10426        2231       OST742   
10427        6327    lncRNA799   

                                             gene_symbol  \
0      ['IGHM', ' SLC7A4', ' IGHV6-1', ' IGHV5-51', '...   
1      ['H4C6', ' H4C12', ' H4C16', ' H4C1', ' H4C4',...   
2      ['H4C1', ' H4C15', ' H4C2', ' H4C5', ' H4C12',...   
3      ['H4C12', ' H4C11', ' H4C4', ' H4C6', ' H4C15'...   
4      ['H4C2', ' H4C4', ' H4C1', ' H4C13', ' H4C5', ...   
...                                                  ...   
10423                                         ['POU5F1']   
10424                                            ['SP7']   
10425                                         ['OSTCP1']   
10426                                          ['OR2C3']   
10427                                      ['LINC03052']   

                                                 ENSG_ID     source  \
0      ENSG00000211899, ENSG00000099960, ENSG00000211...  NCBI Info   
1      ENSG00000274618, ENSG00000273542, ENSG00000197...  NCBI Info   
2      ENSG00000278637, ENSG00000270276, ENSG00000278...  NCBI Info   
3      ENSG00000273542, ENSG00000197238, ENSG00000277...  NCBI Info   
4      ENSG00000278705, ENSG00000277157, ENSG00000278...  NCBI Info   
...                                                  ...        ...   
10423                                    ENSG00000204531       ENSG   
10424                                    ENSG00000291837       ENSG   
10425                                    ENSG00000243775       ENSG   
10426                                    ENSG00000196242       ENSG   
10427                                    ENSG00000292094       ENSG   

       gene_symbol_count  
0                     36  
1                     14  
2                     13  
3                     13  
4                     13  
...                  ...  
10423                  1  
10424                  1  
10425                  1  
10426                  1  
10427                  1  

[10428 rows x 6 columns]

In [6]:
aa_colliison_symbol_list = list(set(merged_alias_overlap_df_2['alias_symbol']))

In [7]:
len(aa_colliison_symbol_list)

9501

In [8]:
def split_list(input_list, chunk_size):
    return [input_list[i:i + chunk_size] for i in range(0, len(input_list), chunk_size)]

# Example usage:
chunked_list = split_list(aa_colliison_symbol_list, 25)
print(chunked_list)

[['LIP1', 'BWS', ' ANT3Y', 'HAP', 'RPD3', 'RECQL3', ' TFB2', 'CT45A6', 'ESF2', 'AAC1', 'L10', 'OR2T2P', 'CT1.2', 'TCRAV20S1', ' DFNB21', ' DDX16', 'C6ORF20', ' EP2', ' P200', 'DPK', ' RW1', 'TANGO', 'B7-H2', 'OI11', 'RN5S116'], ['LST-3TM12', ' DNM1DN14@', 'RFP2', 'KRN1L', 'COPINE-6', ' KNSL2', ' MODY5', ' PRO2389', ' p120', 'FAM189A1', 'CK1', 'HSP27', 'MSS1', 'p62', 'AMGL', 'SPK', 'PSF1', ' MGC1603', 'POTE2beta', ' CG1', ' KAP1.1', ' P55', ' KIAA1899', 'T2R9', ' DJ182D15.1'], ['XCE', ' H3', 'CPD6', 'CPAD', ' C16ORF52', 'PSD', 'ASMTL-AS', ' U4', 'P12', ' DP3', 'CREB2', ' LILRB6', 'RNU1-7P', 'C2orf27B', 'SEP2', 'BA561O23.1', 'NOC', 'JM11', ' CYP2D7P2', 'STAT5', ' HLP2', ' OR7-140', ' XAP104', 'BBP', ' FLJ00101'], ['CLCA3', ' DERLIN-3', ' ULG3', 'K35', 'INT3', 'MLL4', ' PPP1R29', 'SNF2LB', ' KAP4.4', ' PWCR', ' RP58', ' ORF26', 'JLNS1', 'DC2L', ' PERRS', 'RNU1-25', 'TCRAV18S1', 'IGHV(II)-22-1', ' PP2', 'HCG', 'FCG2', 'FLJ42875', ' TC1', ' GL', ' DFNA3'], ['HK4', ' CL-49', 'ADR', 'DP3', 'K

In [9]:
len(chunked_list)

381

In [10]:
# # Define a retry decorator with exponential backoff
# @retry(wait_exponential_multiplier=1000, wait_exponential_max=10000, stop_max_attempt_number=5)
# def make_request(url, params):
#     response = requests.get(url, params=params)
#     if response.status_code != 200:
#         raise Exception(f"Request failed with status code {response.status_code}")
#     return response

# def grab_count(response):
#     try:
#         count = response.text.split("<Count>")[1].split("</Count>")[0]
#         return count
#     except IndexError:
#         print(f"Failed to extract count. Response text: {response.text}")
#         return "Count not found in response"

# gene_list = chunked_list[1]

# abstract_counts = {}

# for gene in gene_list:
#     url = 'https://eutils.ncbi.nlm.nih.gov/entrez/eutils/esearch.fcgi'
#     search_params = {
#         'db': 'pubmed',
#         'term': f'({gene})',
#         'retmax': 0,  # Set retmax to 0 to only get the count of matching items
#         'field': 'abstract'  # Limit search to abstracts
#     }
    
#     try:
#         response = make_request(url, params=search_params)
        
#         # Debugging output to understand response.text
#         print(f"Response for {gene}: {response.text}")
        
#         if "API rate limit exceeded" in response.text:
#             raise Exception("API rate limit exceeded")
        
#         abstract_counts[gene] = grab_count(response)
        
#     except requests.RequestException as e:
#         print(f"RequestException occurred for {gene}: {e}")
#         abstract_counts[gene] = f'Request Exception: {str(e)}'
#     except Exception as e:
#         print(f"Unexpected error occurred for {gene}: {str(e)}")
#         abstract_counts[gene] = f'Unexpected Error: {str(e)}'

# print("Abstract Counts:")
# print(abstract_counts)

In [11]:
# Define a retry decorator with exponential backoff
@retry(wait_exponential_multiplier=1000, wait_exponential_max=10000, stop_max_attempt_number=5)
def make_request(url, params):
    response = requests.get(url, params=params)
    if response.status_code != 200:
        raise Exception(f"Request failed with status code {response.status_code}")
    return response

def grab_count(response):
    try:
        count = response.text.split("<Count>")[1].split("</Count>")[0]
        pmids = [pmid.strip() for pmid in response.text.split("<Id>") if pmid.strip().isdigit()]
        return count, pmids
    except IndexError:
        print(f"Failed to extract count. Response text: {response.text}")
        return "Count not found in response", []

# Example chunked_list (replace with your actual chunked_list)
chunked_list = chunked_list

abstract_counts = {}

# Define the range of sublists to iterate through
start_index = 0  # starting from index 1 (second sublist)
end_index = 380   # ending at index 25 (inclusive)

for sublist in tqdm(chunked_list[start_index:end_index + 1], desc="Processing genes"):  # iterate through index 1 to 25 (inclusive)
    for gene in sublist:
        url = 'https://eutils.ncbi.nlm.nih.gov/entrez/eutils/esearch.fcgi'
        search_params = {
            'db': 'pubmed',
            'term': f'({gene})',
            'retmax': 0,  # Set retmax to 0 to only get the count of matching items
            'field': 'abstract'  # Limit search to abstracts
        }
        
        try:
            response = make_request(url, params=search_params)
            
            # Debugging output to understand response.text
            print(f"Response for {gene}: {response.text}")
            
            if "API rate limit exceeded" in response.text:
                raise Exception("API rate limit exceeded")
            
            abstract_counts[gene] = grab_count(response)
            
        except requests.RequestException as e:
            print(f"RequestException occurred for {gene}: {e}")
            abstract_counts[gene] = f'Request Exception: {str(e)}'
        except Exception as e:
            print(f"Unexpected error occurred for {gene}: {str(e)}")
            abstract_counts[gene] = f'Unexpected Error: {str(e)}'

print("Abstract Counts:")
print(abstract_counts)

Processing genes:   0%|          | 0/381 [00:00<?, ?it/s]

Response for LIP1: <?xml version="1.0" encoding="UTF-8" ?>
<!DOCTYPE eSearchResult PUBLIC "-//NLM//DTD esearch 20060628//EN" "https://eutils.ncbi.nlm.nih.gov/eutils/dtd/20060628/esearch.dtd">
<eSearchResult><Count>262</Count><RetMax>0</RetMax><RetStart>0</RetStart><IdList/><TranslationSet/><QueryTranslation>"LIP1"[All Fields]</QueryTranslation></eSearchResult>

Response for BWS: <?xml version="1.0" encoding="UTF-8" ?>
<!DOCTYPE eSearchResult PUBLIC "-//NLM//DTD esearch 20060628//EN" "https://eutils.ncbi.nlm.nih.gov/eutils/dtd/20060628/esearch.dtd">
<eSearchResult><Count>1906</Count><RetMax>0</RetMax><RetStart>0</RetStart><IdList/><TranslationSet/><QueryTranslation>"BWS"[All Fields]</QueryTranslation></eSearchResult>

Response for  ANT3Y: <?xml version="1.0" encoding="UTF-8" ?>
<!DOCTYPE eSearchResult PUBLIC "-//NLM//DTD esearch 20060628//EN" "https://eutils.ncbi.nlm.nih.gov/eutils/dtd/20060628/esearch.dtd">
<eSearchResult><Count>0</Count><RetMax>0</RetMax><RetStart>0</RetStart><IdList/

Processing genes:   0%|          | 1/381 [00:25<2:41:36, 25.52s/it]

Response for RN5S116: <?xml version="1.0" encoding="UTF-8" ?>
<!DOCTYPE eSearchResult PUBLIC "-//NLM//DTD esearch 20060628//EN" "https://eutils.ncbi.nlm.nih.gov/eutils/dtd/20060628/esearch.dtd">
<eSearchResult><Count>0</Count><RetMax>0</RetMax><RetStart>0</RetStart><IdList/><TranslationSet/><QueryTranslation>(RN5S116)</QueryTranslation><ErrorList><PhraseNotFound>RN5S116</PhraseNotFound></ErrorList><WarningList><OutputMessage>No items found.</OutputMessage></WarningList></eSearchResult>

Response for LST-3TM12: <?xml version="1.0" encoding="UTF-8" ?>
<!DOCTYPE eSearchResult PUBLIC "-//NLM//DTD esearch 20060628//EN" "https://eutils.ncbi.nlm.nih.gov/eutils/dtd/20060628/esearch.dtd">
<eSearchResult><Count>5</Count><RetMax>0</RetMax><RetStart>0</RetStart><IdList/><TranslationSet/><QueryTranslation>"LST-3TM12"[All Fields]</QueryTranslation></eSearchResult>

Response for  DNM1DN14@: <?xml version="1.0" encoding="UTF-8" ?>
<!DOCTYPE eSearchResult PUBLIC "-//NLM//DTD esearch 20060628//EN" "http

Processing genes:   1%|          | 2/381 [00:51<2:42:08, 25.67s/it]

...

Response for  NAIC: <?xml version="1.0" encoding="UTF-8" ?>
<!DOCTYPE eSearchResult PUBLIC "-//NLM//DTD esearch 20060628//EN" "https://eutils.ncbi.nlm.nih.gov/eutils/dtd/20060628/esearch.dtd">
<eSearchResult><Count>71</Count><RetMax>0</RetMax><RetStart>0</RetStart><IdList/><TranslationSet/><QueryTranslation>"NAIC"[All Fields]</QueryTranslation></eSearchResult>

Response for PAPA1: <?xml version="1.0" encoding="UTF-8" ?>
<!DOCTYPE eSearchResult PUBLIC "-//NLM//DTD esearch 20060628//EN" "https://eutils.ncbi.nlm.nih.gov/eutils/dtd/20060628/esearch.dtd">
<eSearchResult><Count>12</Count><RetMax>0</RetMax><RetStart>0</RetStart><IdList/><TranslationSet/><QueryTranslation>"PAPA1"[All Fields]</QueryTranslation></eSearchResult>

Response for KAP9.3: <?xml version="1.0" encoding="UTF-8" ?>
<!DOCTYPE eSearchResult PUBLIC "-//NLM//DTD esearch 20060628//EN" "https://eutils.ncbi.nlm.nih.gov/eutils/dtd/20060628/esearch.dtd">
<eSearchResult><Count>0</Count><RetMax>0</RetMax><RetStart>0</RetStart><IdLis

Processing genes: 100%|█████████▉| 380/381 [2:36:11<00:25, 25.46s/it]

Response for EF-1D: <?xml version="1.0" encoding="UTF-8" ?>
<!DOCTYPE eSearchResult PUBLIC "-//NLM//DTD esearch 20060628//EN" "https://eutils.ncbi.nlm.nih.gov/eutils/dtd/20060628/esearch.dtd">
<eSearchResult><Count>0</Count><RetMax>0</RetMax><RetStart>0</RetStart><IdList/><TranslationSet/><QueryTranslation>(EF-1D)</QueryTranslation><ErrorList><PhraseNotFound>EF-1D</PhraseNotFound></ErrorList><WarningList><OutputMessage>No items found.</OutputMessage></WarningList></eSearchResult>



Processing genes: 100%|██████████| 381/381 [2:36:11<00:00, 24.60s/it]

Response for  DIVA: <?xml version="1.0" encoding="UTF-8" ?>
<!DOCTYPE eSearchResult PUBLIC "-//NLM//DTD esearch 20060628//EN" "https://eutils.ncbi.nlm.nih.gov/eutils/dtd/20060628/esearch.dtd">
<eSearchResult><Count>1204</Count><RetMax>0</RetMax><RetStart>0</RetStart><IdList/><TranslationSet/><QueryTranslation>"DIVA"[All Fields]</QueryTranslation></eSearchResult>

Abstract Counts:
{'LIP1': ('262', []), 'BWS': ('1906', []), ' ANT3Y': ('0', []), 'HAP': ('7960', []), 'RPD3': ('557', []), 'RECQL3': ('5', []), ' TFB2': ('40', []), 'CT45A6': ('0', []), 'ESF2': ('40', []), 'AAC1': ('101', []), 'L10': ('2766', []), 'OR2T2P': ('0', []), 'CT1.2': ('230', []), 'TCRAV20S1': ('0', []), ' DFNB21': ('15', []), ' DDX16': ('1', []), 'C6ORF20': ('0', []), ' EP2': ('2611', []), ' P200': ('1416', []), 'DPK': ('401', []), ' RW1': ('176', []), 'TANGO': ('2023', []), 'B7-H2': ('75', []), 'OI11': ('1', []), 'RN5S116': ('0', []), 'LST-3TM12': ('5', []), ' DNM1DN14@': ('0', []), 'RFP2': ('29', []), 'KRN1L': ('1'

In [12]:
abstract_counts

{'LIP1': ('262', []),
 'BWS': ('1906', []),
 ' ANT3Y': ('0', []),
 'HAP': ('7960', []),
 'RPD3': ('557', []),
 'RECQL3': ('5', []),
 ' TFB2': ('40', []),
 'CT45A6': ('0', []),
 'ESF2': ('40', []),
 'AAC1': ('101', []),
 'L10': ('2766', []),
 'OR2T2P': ('0', []),
 'CT1.2': ('230', []),
 'TCRAV20S1': ('0', []),
 ' DFNB21': ('15', []),
 ' DDX16': ('1', []),
 'C6ORF20': ('0', []),
 ' EP2': ('2611', []),
 ' P200': ('1416', []),
 'DPK': ('401', []),
 ' RW1': ('176', []),
 'TANGO': ('2023', []),
 'B7-H2': ('75', []),
 'OI11': ('1', []),
 'RN5S116': ('0', []),
 'LST-3TM12': ('5', []),
 ' DNM1DN14@': ('0', []),
 'RFP2': ('29', []),
 'KRN1L': ('1', []),
 'COPINE-6': ('19', []),
 ' KNSL2': ('3', []),
 ' MODY5': ('134', []),
 ' PRO2389': ('0', []),
 ' p120': ('2091', []),
 'FAM189A1': ('8', []),
 'CK1': ('1146', []),
 'HSP27': ('5086', []),
 'MSS1': ('60', []),
 'p62': ('11729', []),
 'AMGL': ('12', []),
 'SPK': ('1431', []),
 'PSF1': ('86', []),
 ' MGC1603': ('0', []),
 'POTE2beta': ('1', []),
 '

In [13]:
len(abstract_counts)

9501

In [15]:
abstract_counts_df = pd.DataFrame(list(abstract_counts.items()), columns=['ambiguous symbol', 'number of abstracts with a match'])

# Strip leading and trailing spaces from column names (optional)
abstract_counts_df.columns = abstract_counts_df.columns.str.strip()
abstract_counts_df['number of abstracts with a match'] = abstract_counts_df['number of abstracts with a match'].apply(lambda x: x[0])


abstract_counts_df

ambiguous symbol number of abstracts with a match
0                LIP1                              262
1                 BWS                             1906
2               ANT3Y                                0
3                 HAP                             7960
4                RPD3                              557
...               ...                              ...
9496             NOMO                              144
9497           SPBC25                                1
9498        EST123147                                0
9499            EF-1D                                0
9500             DIVA                             1204

[9501 rows x 2 columns]

In [16]:
abstract_counts_df['number of abstracts with a match'] = abstract_counts_df['number of abstracts with a match'].astype(int)

In [23]:
abstract_counts_df.to_csv('abstract_counts_df.csv', index=True)

In [18]:
sum_counts = abstract_counts_df['number of abstracts with a match'].sum()
sum_counts

254154181

In [19]:
# Enable caching with a SQLite database
requests_cache.install_cache('pubmed_cache', backend='sqlite', expire_after=3600)  # Cache expires after 1 hour

In [20]:
def search_pubmed_for_gene_symbols(gene_symbols_file):
    base_url = "https://eutils.ncbi.nlm.nih.gov/entrez/eutils/"
    search_url = base_url + "esearch.fcgi"
    
    with open(gene_symbols_file, 'r') as f:
        gene_symbols = [line.strip() for line in f.readlines()]

    batch_size = 10  # Adjust batch size to manage query length
    num_batches = 1 #(len(gene_symbols) + batch_size - 1) // batch_size

    results = {'Gene Symbol': [], 'Number of Matches in Abstracts': []}  # Dictionary to store results for each gene symbol

    for i in range(num_batches):
        batch_symbols = gene_symbols[i * batch_size : (i + 1) * batch_size]
        query = '("' + '" OR "'.join(batch_symbols) + '")'
        encoded_query = quote_plus(query)

        search_params = {
            'db': 'pubmed',
            'term': encoded_query,
            'retmax': 0,  # Set retmax to 0 to only get the count of matching items
            'field': 'abstract'  # Limit search to abstracts
        }

        try:
            print(search_url)
            response = requests.get(search_url, params=search_params)
            print(search_params)
            print()
            print(response.text)
            response.raise_for_status()  # Raise an exception for HTTP errors

            if response.status_code == 200:
                pmids = response.text.splitlines()
                for symbol in batch_symbols:
                    results['Gene Symbol'].append(symbol)
                    results['Number of Matches in Abstracts'].append(len(pmids))
            else:
                print(f"Error in PubMed search (batch {i}): {response.status_code}")
        
        except requests.RequestException as e:
            print(f"Error in connection (batch {i}): {e}")

# Create DataFrame
    df = pd.DataFrame(results)

    # Display DataFrame
    print(df)

    # Optionally, you can save the DataFrame to a CSV file
    df.to_csv('pubmed_results.csv', index=False)

https://eutils.ncbi.nlm.nih.gov/entrez/eutils/esearch.fcgi?db=pubmed&term=(%22VH%22%20OR%20%22H4-16%22)&retmax=0

In [21]:
# Usage example
df = search_pubmed_for_gene_symbols("aa_colliison_symbol_listpart1a.txt")

https://eutils.ncbi.nlm.nih.gov/entrez/eutils/esearch.fcgi
{'db': 'pubmed', 'term': '%28%22VH%22+OR+%22H4-16%22+OR+%22H4C13%22+OR+%22H4C1%22+OR+%22H4C12%22+OR+%22H4C14%22+OR+%22H4C15%22+OR+%22H4C2%22+OR+%22H4C3%22+OR+%22H4C4%22%29', 'retmax': 0, 'field': 'abstract'}

<?xml version="1.0" encoding="UTF-8" ?>
<!DOCTYPE eSearchResult PUBLIC "-//NLM//DTD esearch 20060628//EN" "https://eutils.ncbi.nlm.nih.gov/eutils/dtd/20060628/esearch.dtd">
<eSearchResult><Count>0</Count><RetMax>0</RetMax><RetStart>0</RetStart><IdList/><TranslationSet/><QueryTranslation>"28"[All Fields] AND "22 or"[All Fields] AND "22 or"[All Fields] AND "22 or"[All Fields] AND "22 or"[All Fields] AND "22 or"[All Fields] AND "22 or"[All Fields] AND "22 or"[All Fields] AND "22 or"[All Fields] AND "22 or"[All Fields] AND "22 29"[All Fields]</QueryTranslation><ErrorList><PhraseNotFound>22VH</PhraseNotFound><PhraseNotFound>22H4-16</PhraseNotFound><PhraseNotFound>22H4C13</PhraseNotFound><PhraseNotFound>22H4C1</PhraseNotFound><P

In [22]:
df